In [1]:
import os
import pandas as pd
import shutil
import json
from tqdm import tqdm
from tqdm.auto import tqdm

In [2]:
synthesis_subjects = pd.read_csv('./xai-synthesis.csv')

In [3]:
synthesis_subjects.head()

Unnamed: 0                                         solution_0  \
0  leetcode_python_0387  \nclass Solution:\n    def firstUniqChar(self,...   
1  leetcode_python_0389  \nclass Solution:\n    def findTheDifference(s...   
2  leetcode_python_0394  \nimport re\n\ndef decodeString(s):\n    def d...   
3  leetcode_python_0396  \nclass Solution:\n    def maxRotateFunction(s...   
4  leetcode_python_0397  \nclass Solution:\n    def integerReplacement(...   

                                          solution_1  \
0  \nclass Solution:\n    def firstUniqChar(self,...   
1  \nclass Solution:\n    def findTheDifference(s...   
2  \nimport re\n\ndef decodeString(s):\n    def d...   
3  \nclass Solution:\n    def maxRotateFunction(s...   
4  \nclass Solution:\n    def integerReplacement(...   

                                          solution_2  \
0  \nclass Solution:\n    def firstUniqChar(self,...   
1  \nclass Solution:\n    def findTheDifference(s...   
2  \nimport re\n\ndef decodeString(s):\n    def d...   
3  \nclass Solution:\n    def maxRotateFunction(s...   
4  \nclass Solution:\n    def integerReplacement(...   

                                          solution_3  \
0  \nclass Solution:\n    def firstUniqChar(self,...   
1  \nclass Solution:\n    def findTheDifference(s...   
2  \nimport re\n\ndef decodeString(s):\n    def d...   
3  \nclass Solution:\n    def maxRotateFunction(s...   
4  \nclass Solution:\n    def integerReplacement(...   

                                          solution_4  \
0  \nclass Solution:\n    def firstUniqChar(self,...   
1  \nclass Solution:\n    def findTheDifference(s...   
2  \nimport re\n\ndef decodeString(s):\n    def d...   
3  \nclass Solution:\n    def maxRotateFunction(s...   
4  \nclass Solution:\n    def integerReplacement(...   

                                          solution_5  \
0  \nclass Solution:\n    def firstUniqChar(self,...   
1  \nclass Solution:\n    def findTheDifference(s...   
2  \nimport re\n\ndef decodeString(s):\n    def d...   
3  \nclass Solution:\n    def maxRotateFunction(s...   
4  \nclass Solution:\n    def integerReplacement(...   

                                          solution_6  \
0  \nclass Solution:\n    def firstUniqChar(self,...   
1  \nclass Solution:\n    def findTheDifference(s...   
2  \nimport re\n\ndef decodeString(s):\n    def d...   
3  \nclass Solution:\n    def maxRotateFunction(s...   
4  \nclass Solution:\n    def integerReplacement(...   

                                          solution_7  \
0  \nclass Solution:\n    def firstUniqChar(self,...   
1  \nclass Solution:\n    def findTheDifference(s...   
2  \nimport re\n\ndef decodeString(s):\n    def d...   
3  \nclass Solution:\n    def maxRotateFunction(s...   
4  \nclass Solution:\n    def integerReplacement(...   

                                          solution_8  ...  \
0  \nclass Solution:\n    def firstUniqChar(self,...  ...   
1  \nclass Solution:\n    def findTheDifference(s...  ...   
2  \nimport re\n\ndef decodeString(s):\n    def d...  ...   
3  \nclass Solution:\n    def maxRotateFunction(s...  ...   
4  \nclass Solution:\n    def integerReplacement(...  ...   

                                         solution_40  \
0  \nclass Solution:\n    def firstUniqChar(self,...   
1  \nclass Solution:\n    def findTheDifference(s...   
2  \nimport re\n\ndef decodeString(s):\n    def d...   
3  \nclass Solution:\n    def maxRotateFunction(s...   
4  \nclass Solution:\n    def integerReplacement(...   

                                         solution_41  \
0  \nclass Solution:\n    def firstUniqChar(self,...   
1  \nclass Solution:\n    def findTheDifference(s...   
2  \nimport re\n\ndef decodeString(s):\n    def d...   
3  \nclass Solution:\n    def maxRotateFunction(s...   
4  \nclass Solution:\n    def integerReplacement(...   

                                         solution_42  \
0  \nclass Solution:\n    def firstUniqChar(self,...   
1  \nclass Solution:\n    def fi

In [4]:
result = {"program_id": [], "solution_id": [], "passing": [], "failing": []}

In [5]:
imports = """
import random
import typing
from typing import *
import collections
from collections import *
import functools
from functools import *
import math
from math import *
import string
from string import *
import bisect
import heapq
from heapq import *
import itertools
from itertools import *
import re
from re import *
import operator
class ListNode:
    def __init__(self, val=0, next=None):
        self.val = val
        self.next = next

    def __eq__(self, other):
        if other is None:
            return False
        return self.val == other.val and self.next == other.next

    def __repr__(self):
        return f"ListNode({self.val}, {self.next})"


class TreeNode:
    def __init__(self, val=0, left=None, right=None):
        self.val = val
        self.left = left
        self.right = right

    def __eq__(self, other):
        if other is None:
            return False
        return (
            self.val == other.val
            and self.left == other.left
            and self.right == other.right
        )

    def __repr__(self):
        return f"TreeNode({self.val}, {self.left}, {self.right})"

"""


In [6]:
for index, row in tqdm(synthesis_subjects.iterrows(),total = synthesis_subjects.shape[0]):
    problem_id, *solutions = row
    #print(solutions)
    internal_problem_id = problem_id.split("_")[-1]

    for i, solution in tqdm(enumerate(solutions), total=len(solutions)):
        body = imports + "\n\n" + solution
        with open(
            os.path.join("py-suite", internal_problem_id, "solution.py"), "w"
        ) as f:
            f.write(body)

        os.system(
            "cd {} && pytest --json-report --json-report-summary --timeout=10".format(
                os.path.join("py-suite", internal_problem_id)
            )
        )
        passed = -1
        failed = -1
        with open( os.path.join("py-suite", internal_problem_id,".report.json")) as g:
            report = json.load(g)
            passed = report["summary"].get("passed",0)
            failed = report["summary"]["total"] - passed

        result["program_id"].append(f"{problem_id}")
        result["solution_id"].append(f"{solution}_{i}")
        result["passing"].append(passed)
        result["failing"].append(failed)
        #print(f"Submission {i} for {problem_id}, Passed: {passed}, Failed: {failed}")
        

  0%|          | 0/1063 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

============================= test session starts ==============================
platform linux -- Python 3.11.7, pytest-7.4.3, pluggy-1.3.0
rootdir: /home/marti_2203/Desktop/NUS/XAI/LeetCode-walkccc/py-suite/0387
plugins: black-0.3.12, anyio-4.2.0, asyncio-0.21.1, xdist-3.5.0, hypothesis-6.92.2, cov-4.1.0, timeout-2.2.0, metadata-3.0.0, json-report-1.5.0
asyncio: mode=Mode.STRICT
timeout: 10.0s
timeout method: signal
timeout func_only: False
collected 20 items

test_0.py .                                                              [  5%]
test_1.py .                                                              [ 10%]
test_10.py .                                                             [ 15%]
test_11.py .                                                             [ 20%]
test_12.py .                                                             [ 25%]
test_13.py .                                                             [ 30%]
test_14.py .                                         

  0%|          | 0/50 [00:00<?, ?it/s]

============================= test session starts ==============================
platform linux -- Python 3.11.7, pytest-7.4.3, pluggy-1.3.0
rootdir: /home/marti_2203/Desktop/NUS/XAI/LeetCode-walkccc/py-suite/0389
plugins: black-0.3.12, anyio-4.2.0, asyncio-0.21.1, xdist-3.5.0, hypothesis-6.92.2, cov-4.1.0, timeout-2.2.0, metadata-3.0.0, json-report-1.5.0
asyncio: mode=Mode.STRICT
timeout: 10.0s
timeout method: signal
timeout func_only: False
collected 20 items

test_0.py F                                                              [  5%]
test_1.py F                                                              [ 10%]
test_10.py F                                                             [ 15%]
test_11.py F                                                             [ 20%]
test_12.py F                                                             [ 25%]
test_13.py F                                                             [ 30%]
test_14.py F                                         

...

============================= test session starts ==============================
platform linux -- Python 3.11.7, pytest-7.4.3, pluggy-1.3.0
rootdir: /home/marti_2203/Desktop/NUS/XAI/LeetCode-walkccc/py-suite/0397
plugins: black-0.3.12, anyio-4.2.0, asyncio-0.21.1, xdist-3.5.0, hypothesis-6.92.2, cov-4.1.0, timeout-2.2.0, metadata-3.0.0, json-report-1.5.0
asyncio: mode=Mode.STRICT
timeout: 10.0s
timeout method: signal
timeout func_only: False
collected 20 items

test_0.py F                                                              [  5%]
test_1.py F                                                              [ 10%]
test_10.py F                                                             [ 15%]
test_11.py .                                                             [ 20%]
test_12.py F                                                             [ 25%]
test_13.py F                                                             [ 30%]
test_14.py F                                         

  0%|          | 0/50 [00:00<?, ?it/s]

============================= test session starts ==============================
platform linux -- Python 3.11.7, pytest-7.4.3, pluggy-1.3.0
rootdir: /home/marti_2203/Desktop/NUS/XAI/LeetCode-walkccc/py-suite/0400
plugins: black-0.3.12, anyio-4.2.0, asyncio-0.21.1, xdist-3.5.0, hypothesis-6.92.2, cov-4.1.0, timeout-2.2.0, metadata-3.0.0, json-report-1.5.0
asyncio: mode=Mode.STRICT
timeout: 10.0s
timeout method: signal
timeout func_only: False
collected 20 items

test_0.py .                                                              [  5%]
test_1.py F                                                              [ 10%]
test_10.py F                                                             [ 15%]
test_11.py F                                                             [ 20%]
test_12.py F                                                             [ 25%]
test_13.py F                                                             [ 30%]
test_14.py F                                         

  0%|          | 0/50 [00:00<?, ?it/s]

============================= test session starts ==============================
platform linux -- Python 3.11.7, pytest-7.4.3, pluggy-1.3.0
rootdir: /home/marti_2203/Desktop/NUS/XAI/LeetCode-walkccc/py-suite/0403
plugins: black-0.3.12, anyio-4.2.0, asyncio-0.21.1, xdist-3.5.0, hypothesis-6.92.2, cov-4.1.0, timeout-2.2.0, metadata-3.0.0, json-report-1.5.0
asyncio: mode=Mode.STRICT
timeout: 10.0s
timeout method: signal
timeout func_only: False
collected 0 items / 20 errors

==================================== ERRORS ====================================
__________________________ ERROR collecting test_0.py __________________________
/usr/lib/python3.11/site-packages/_pytest/python.py:617: in _importtestmodule
    mod = import_path(self.path, mode=importmode, root=self.config.rootpath)
/usr/lib/python3.11/site-packages/_pytest/pathlib.py:567: in import_path
    importlib.import_module(module_name)
/usr/lib64/python3.11/importlib/__init__.py:126: in import_module
    return _bootstrap._gc

In [ ]:
pd.DataFrame(result).to_csv("synthesis-py-eval-results.csv", index=False)